In [1]:
from nba_api.stats.endpoints import commonplayerinfo, playercareerstats, leaguegamefinder, commonteamroster, leagueseasonmatchups
from nba_api.stats.static import players, teams
from os import path
import pandas as pd
import pickle
import numpy as np

In [2]:
""" for saving and loading things to a pickle file. Don't need to add extension to the file name """
def save_obj(obj, filename, dirname='pickle_files', ):
    with open(path.join(dirname, filename + '.pkl'), 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

def load_obj(filename, dirname='pickle_files'):
    with open(path.join(dirname, filename + '.pkl'), 'rb') as f:
        return pickle.load(f)

In [5]:
teams_df = pd.DataFrame(teams.get_teams())
teams_df.head()

id             full_name abbreviation   nickname         city  \
0  1610612737         Atlanta Hawks          ATL      Hawks      Atlanta   
1  1610612738        Boston Celtics          BOS    Celtics       Boston   
2  1610612739   Cleveland Cavaliers          CLE  Cavaliers    Cleveland   
3  1610612740  New Orleans Pelicans          NOP   Pelicans  New Orleans   
4  1610612741         Chicago Bulls          CHI      Bulls      Chicago   

           state  year_founded  
0        Atlanta          1949  
1  Massachusetts          1946  
2           Ohio          1970  
3      Louisiana          2002  
4       Illinois          1966

In [6]:
team_ids = teams_df.loc[:, ("id","abbreviation")]

In [7]:
team_ids["abbreviation"]

0     ATL
1     BOS
2     CLE
3     NOP
4     CHI
5     DAL
6     DEN
7     GSW
8     HOU
9     LAC
10    LAL
11    MIA
12    MIL
13    MIN
14    BKN
15    NYK
16    ORL
17    IND
18    PHI
19    PHX
20    POR
21    SAC
22    SAS
23    OKC
24    TOR
25    UTA
26    MEM
27    WAS
28    DET
29    CHA
Name: abbreviation, dtype: object

# Normalizing 

In [41]:
# seasons = list(range(22009, 22019))
# season_avgs = {}
# for s in seasons:
#     team_averages = np.zeros(19)
#     for i in team_ids["id"]:
#         teams_df = get_season_team(s, i, team_names_test)
#         team_averages += get_team_avgs(teams_df, num_rows(teams_df), num_rows(teams_df) - 1)
#     season_avgs[s] = team_averages / len(team_ids["id"])

In [57]:
df = get_season_team(22018, 1610612737, team_names_test)
df = df.drop(df.columns[list(range(0, 9))], axis = 1).values.tolist()

In [63]:
from sklearn.preprocessing import StandardScaler

In [65]:
def normalize(prev_season):
    scaler = StandardScaler()
    season = []
    for i in team_ids["id"]:
        teams_df = get_season_team(prev_season, i, team_names_test)
        teams_list = teams_df.drop(teams_df.columns[list(range(0, 9))], axis = 1).values.tolist()
        season += teams_list
    
    scaler.fit(season)
    return scaler

In [ ]:
normalize(team_names_test[1610612737], by_header="")

In [64]:
# *** should only have to run the loading cell below ***
# get team info into dataframes
# store dictionary key = team abbreviation, value = df with game data
import time

team_names = {}
for i in range(len(team_ids)): 
    temp_id = team_ids["id"][i]
    temp_team_name = team_ids["abbreviation"][i]
    print('getting team: {0}...'.format(temp_team_name))
    team_names[temp_team_name] = leaguegamefinder.LeagueGameFinder(team_id_nullable=temp_id).get_data_frames()[0]
    time.sleep(1)

getting team: ATL...


ReadTimeout: HTTPSConnectionPool(host='stats.nba.com', port=443): Read timed out. (read timeout=30)

In [6]:
""" save dictionary to a file called team_names under pickle_files folder"""
# save_obj(team_names, 'team_names')

NameError: name 'team_names' is not defined

# Messy Calculations

In [8]:
""" load the team_names dictionary in pickle_files """
team_names = load_obj('team_names')

In [9]:
team_names_test = {}

ids = team_ids["id"]
abr = team_ids["abbreviation"]

for i in range(len(ids)):
    real_value = team_names[abr[i]]
    test_key = ids[i]
    team_names_test[test_key] = real_value

In [44]:
# for game in team_names['CHA'].values.tolist():
#     if (game[2] != "CHA"):
#         print(game[2])

all_abrs = {}
for team in team_names.keys():
    df = team_names[team]
    abrs = set()
    for game in df.values.tolist():
        abrs.add(game[2])
    for abr in abrs:
        all_abrs[abr] = df
#print(len(all_abrs))
all_abrs['ATL']

SEASON_ID     TEAM_ID TEAM_ABBREVIATION      TEAM_NAME     GAME_ID  \
0        22019  1610612737               ATL  Atlanta Hawks  0021900105   
1        22019  1610612737               ATL  Atlanta Hawks  0021900099   
2        22019  1610612737               ATL  Atlanta Hawks  0021900066   
3        22019  1610612737               ATL  Atlanta Hawks  0021900052   
4        22019  1610612737               ATL  Atlanta Hawks  0021900043   
...        ...         ...               ...            ...         ...   
3247     21983  1610612737               ATL  Atlanta Hawks  0028300058   
3248     21983  1610612737               ATL  Atlanta Hawks  0028300041   
3249     21983  1610612737               ATL  Atlanta Hawks  0028300027   
3250     21983  1610612737               ATL  Atlanta Hawks  0028300014   
3251     21983  1610612737               ATL  Atlanta Hawks  0028300005   

       GAME_DATE      MATCHUP    WL  MIN  PTS  ...  FT_PCT  OREB  DREB  REB  \
0     2019-11-06  ATL vs. CHI  None   24    8  ...   1.000     1     3    4   
1     2019-11-05  ATL vs. SAS     W  240  108  ...   0.688     9    39   48   
2     2019-10-31  ATL vs. MIA     L  238   97  ...   0.692    16    34   50   
3     2019-10-29    ATL @ MIA     L  240   97  ...   0.667     9    24   33   
4     2019-10-28  ATL vs. PHI     L  240  103  ...   0.688     8    37   45   
...          ...          ...   ...  ...  ...  ...     ...   ...   ...  ...   
3247  1983-11-06    ATL @ MIL     L  240   84  ...   0.667    11    26   37   
3248  1983-11-04  ATL vs. CHI     W  240  103  ...   0.692    19    27   46   
3249  1983-11-01  ATL vs. WAS     W  240   95  ...   0.633    12    29   41   
3250  1983-10-29  ATL vs. DET     W  240  117  ...   0.633    27    21   48   
3251  1983-10-28    ATL @ NJN     L  240  108  ...   0.684    15    18   33   

      AST   STL  BLK  TOV  PF  PLUS_MINUS  
0       1   0.0    0    3   0        -9.0  
1      22   9.0    5   18  20         8.0  
2      20   5.0    5   16  15        -9.0  
3      28  14.0    7   20  29       -15.0  
4      23  12.0    3   21  25        -2.0  
...   ...   ...  ...  ...  ..         ...  
3247   18   4.0    5   14  24         NaN  
3248   31  14.0   13   18  27         NaN  
3249   20   7.0   10   16  34         NaN  
3250   28  14.0    7   23  35         NaN  
3251   14  10.0    5   17  30         NaN  

[3252 rows x 28 columns]

In [150]:
""" gets the season games given the seasonID and abbreviation of the team """
""" Season is based on the year that the season STARTED in. I.E 2016-2017 has seasonID 2016"""
""" Reg season starts with 2, playoffs 4, pre 1 """
""" 
For some reason summer league and preseason games are sometimes included in reg season IDs.
The function accounts for this by only looking at Game IDs that start with 0021 for reg reason,
0041 for playoffs, 0011 for preseason
"""

def get_season_team(seasonID, team_id, team_names):
    seasonID = str(seasonID)
    gameID_prefix = seasonID[0]
    return team_names[team_id].loc[(team_names[team_id]["SEASON_ID"].str.contains(seasonID)) & \
                                    (team_names[team_id]['GAME_ID'].str.startswith('00{0}'.format(gameID_prefix)))]


""" gets the number of rows in the passed df"""
def num_rows(df):
    return len(df.index)

""" returns the number of features of the df"""
def num_features(df):
    return len(df.columns)

""" returns a list of the features from the start index moving forward. Using 9 for now """
def get_features(df, start_idx=9):
    return [feature for feature in df.columns.tolist()[start_idx:]]

""" 
util func: gets last n games given the curr game
in the df with the correct season, year
"""
def last_n_games(df, n, curr_game):
    n_rows = num_rows(df)
    # the first row is the latest game. I.E for reg season it's 82nd game
    
"""
returns avg team stats vector over the last n games given
the current game. Assumes games 0 indexed
"""
def get_team_avgs(season_games, curr_game, n):
    total_games = num_rows(season_games)
    assert curr_game > n, "curr game ({0}) > n ({1})".format(curr_game, n)
    assert total_games > n, "n ({0}) is more than the total number of games ({1})".format(n, total_games)
    # the real index of the current game
    game_idx = total_games - curr_game - 1
    # start at 9th index to get meaningful stats
    start_idx = 9
    team_avgs = np.zeros(num_features(season_games) - start_idx)
    for i in range(game_idx - n, game_idx):
        game_stats = np.array(season_games.iloc[i].tolist()[start_idx:])
        team_avgs += game_stats
    return team_avgs / n

def print_team_avgs(season_games, team_avgs):
    features = get_features(season_games)
    for stat, feature in zip(team_avgs, features):
        print("{0}:{1}".format(feature, stat))

In [151]:
""" 
get the 2018 season games for the Atlanta Hawks. 
"""
atl_reg_season = get_season_team(22018, 1610612737, team_names_test)
"""
print the avgs of the 10 games before the 16th game that the Hawks played in the 2017-2018 season
"""
atl_team_avgs = get_team_avgs(atl_reg_season, 16, 10)
#print_team_avgs(atl_reg_season, atl_team_avgs)

In [152]:
def find_opponent_id(opp_abr, season_id):
    
    return all_abrs[opp_abr].loc[all_abrs[opp_abr]["SEASON_ID"].str.contains(str(season_id))]["TEAM_ID"].iloc[0]

In [153]:
def find_opponent(n, curr_team, season_id):
    full_df = get_season_team(season_id, curr_team, team_names_test).reset_index()
    
    df_of_game = full_df.iloc[[-n]]
    opp_abr = df_of_game["MATCHUP"].values[0][-3::]
    return find_opponent_id(opp_abr, season_id)

In [154]:
"""get the opponent of the Atlanta Hawks's 2nd game of the the 2018 season"""

find_opponent(2, 1610612737, 22018)

1610612763

In [155]:
def convert_to_01s(letter):
    return 1 if letter == "W" else 0

In [156]:
"""
return the difference vector
"""
def find_diff_vector(curr_game, n, curr_team, season_id):
    #curr_team_season is a df
    curr_team_season = get_season_team(season_id, curr_team, team_names_test)
    curr_team_avgs = get_team_avgs(curr_team_season, curr_game, n)
    
    # find win/loss for single curr_game
    outcome = curr_team_season["WL"].iloc[num_rows(curr_team_season) - curr_game - 1]
    outcome = convert_to_01s(outcome)
    
    opponent = find_opponent(curr_game, curr_team, season_id)
    opponent_team_season = get_season_team(season_id, opponent, team_names_test)
    opponent_team_avgs = get_team_avgs(opponent_team_season, curr_game, n)
    
    # normalize 
    scaler = normalize(season_id - 1)
    curr_team_avgs_normalized = scaler.transform([curr_team_avgs])
    opp_team_avgs_normalized = scaler.transform([opponent_team_avgs])
    
    diff = np.subtract(curr_team_avgs_normalized, opp_team_avgs_normalized)
   
    return diff, outcome

In [157]:
"""diff vector between Atlanta Hawks' stats and its opponents' stats on the Hawks' 16th game
based on the averages of the last 15 games before the nth game"""
find_diff_vector(16, 15, 1610612737, 22009)

(array([[ 0.72919029,  0.72613061,  0.31346485,  0.54419667,  0.6302605 ,
          0.59453668,  0.50747116, -0.04157351,  0.16360691, -0.55983229,
         -0.45811275,  0.20732508, -0.10305272,  0.77196874,  0.22905776,
         -0.13274252, -0.63483003, -0.16810066,  0.89223957]]), 0)

In [77]:
# gets diff vectors for all the games 2-82 for given team and season
def get_season_diff_vectors(curr_team, season_id):
    diff_vector = []
    win_losses = []
    df_len = num_rows(get_season_team(season_id, curr_team, team_names_test))
    for i in range(2, df_len):
        diff, outcome = find_diff_vector(i, i-1, curr_team, season_id)
        diff_vector.append(diff)
        win_losses.append(outcome)
    return diff_vector, win_losses

In [79]:
get_season_diff_vectors(1610612737, 22009)

([array([[ 0.55886847,  1.94499272,  1.47776285,  1.30898087,  0.32599681,
           0.17150096,  0.39576014, -2.18260938, -2.45410371,  0.39937973,
          -0.26429582, -0.19436727, -0.30915815,  1.828347  ,  0.        ,
           0.79645513, -0.51472705, -2.7507381 ,  1.33835936]]),
  array([[-0.83830271, -0.77799709, -1.34342077,  0.13635217, -0.97799043,
           0.        , -1.52409758,  0.07795034,  0.19374503, -0.47820467,
          -2.11436656,  0.09718363, -1.15934306, -2.43779601, -1.20255325,
           2.1902516 ,  0.77209057, -0.34384226, -1.07812282]]),
  array([[ 0.45241733,  1.10216254,  1.11951731,  0.41814667, -0.54332801,
          -0.11433398, -0.71012281, -0.62360268, -0.25832671, -0.99844932,
          -0.70478885, -0.45352362, -0.77289538, -0.20314967, -0.45811552,
           0.79645513, -0.85787842,  0.68768453, -0.76831741]]),
  array([[ 0.79838353,  1.16699563,  0.50378279,  0.92264971,  0.48899521,
          -0.04287524,  0.74941814, -0.54565235, -0.484

In [160]:
# get difference vectors for all teams for one season

def diff_vectors_per_season(season_id):
    team_per_season_dict = {}
    outcomes_per_season_dict = {}
    
    for team in team_ids["id"]:
        #print(team)
        diff, outcomes = get_season_diff_vectors(team, season_id)
        team_per_season_dict[team] = diff
        outcomes_per_season_dict[team] = outcomes
    
    return team_per_season_dict, outcomes_per_season_dict

In [82]:
diff_vectors_per_season(22009)

1610612737
1610612738
1610612739
1610612740
1610612741
1610612742
1610612743
1610612744
1610612745
1610612746
1610612747
1610612748
1610612749
1610612750
1610612751
1610612752
1610612753
1610612754
1610612755
1610612756
1610612757
1610612758
1610612759
1610612760
1610612761
1610612762
1610612763
1610612764
1610612765
1610612766


({1610612737: [array([[ 0.55886847,  1.94499272,  1.47776285,  1.30898087,  0.32599681,
            0.17150096,  0.39576014, -2.18260938, -2.45410371,  0.39937973,
           -0.26429582, -0.19436727, -0.30915815,  1.828347  ,  0.        ,
            0.79645513, -0.51472705, -2.7507381 ,  1.33835936]]),
   array([[-0.83830271, -0.77799709, -1.34342077,  0.13635217, -0.97799043,
            0.        , -1.52409758,  0.07795034,  0.19374503, -0.47820467,
           -2.11436656,  0.09718363, -1.15934306, -2.43779601, -1.20255325,
            2.1902516 ,  0.77209057, -0.34384226, -1.07812282]]),
   array([[ 0.45241733,  1.10216254,  1.11951731,  0.41814667, -0.54332801,
           -0.11433398, -0.71012281, -0.62360268, -0.25832671, -0.99844932,
           -0.70478885, -0.45352362, -0.77289538, -0.20314967, -0.45811552,
            0.79645513, -0.85787842,  0.68768453, -0.76831741]]),
   array([[ 0.79838353,  1.16699563,  0.50378279,  0.92264971,  0.48899521,
           -0.04287524,  0.749

In [161]:
# get diff vectors for all seasons for all teams

def ultimate_diff_vectors():
    ultimate_dict = {}
    ultimate_dict_outcomes = {}
    seasons = list(range(22009, 22019))

    for s in seasons:
        print(s)
        diff, outcomes = diff_vectors_per_season(s)
        ultimate_dict[s] = diff
        ultimate_dict_outcomes[s] = outcomes
        
    return ultimate_dict, ultimate_dict_outcomes

In [162]:
"""
key = season
value = dictionary with key as team id, values as difference numpy arrays
"""
ultimate_dict_normalized, ultimate_dict_outcomes_normalized = ultimate_diff_vectors()


22009
22010
22011
22012
22013
22014
22015
22016
22017
22018


In [33]:
# pickle the ultimate dicts PRE normalizing

#save_obj(ultimate_dict, 'ultimate_dict')
#ultimate_dict_pickled = load_obj('ultimate_dict')

#save_obj(ultimate_dict_outcomes, 'ultimate_dict_outcomes')
#ultimate_dict_outcomes_pickled = load_obj('ultimate_dict_outcomes')

In [163]:
# pickle the ultimate dicts POST normalizing

save_obj(ultimate_dict_normalized, 'ultimate_dict_normalized')
ultimate_dict_pickled = load_obj('ultimate_dict_normalized')

save_obj(ultimate_dict_outcomes_normalized, 'ultimate_dict_outcomes_normalized')
ultimate_dict_outcomes_pickled_normalized = load_obj('ultimate_dict_outcomes_normalized')

## MODELS

In [84]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from pipeline import Model

In [93]:
list(ultimate_dict_pickled.values())[:5]

[{1610612737: [array([  7.   ,  10.   ,  11.   ,   0.072,   1.   ,   1.   ,   0.047,
          -14.   , -19.   ,   0.038,  -1.   ,  -1.   ,  -2.   ,   9.   ,
            0.   ,   2.   ,  -2.   , -12.   ,  18.   ]),
   array([-1.05e+01, -4.00e+00, -1.00e+01,  7.50e-03, -3.00e+00,  0.00e+00,
          -1.81e-01,  5.00e-01,  1.50e+00, -4.55e-02, -8.00e+00,  5.00e-01,
          -7.50e+00, -1.20e+01, -3.50e+00,  5.50e+00,  3.00e+00, -1.50e+00,
          -1.45e+01]),
   array([  5.66666667,   5.66666667,   8.33333333,   0.023     ,
           -1.66666667,  -0.66666667,  -0.08433333,  -4.        ,
           -2.        ,  -0.095     ,  -2.66666667,  -2.33333333,
           -5.        ,  -1.        ,  -1.33333333,   2.        ,
           -3.33333333,   3.        , -10.33333333]),
   array([ 1.000e+01,  6.000e+00,  3.750e+00,  5.075e-02,  1.500e+00,
          -2.500e-01,  8.900e-02, -3.500e+00, -3.750e+00, -1.150e-02,
          -2.250e+00, -2.000e+00, -4.250e+00,  6.750e+00, -1.000e+00,
      

In [145]:
def massive_flatten(ultimate_lists):
    flattened_values = []
    for team in ultimate_lists.values():
        for games in team.values():
            flattened_values.extend(games)
    return flattened_values

In [146]:
X = massive_flatten(ultimate_dict_pickled)
y = massive_flatten(ultimate_dict_outcomes)

In [147]:
Xtr, Xte, ytr, yte = train_test_split(X, y, test_size=0.25)

In [148]:
m = Model(LogisticRegression(solver='lbfgs', multi_class='multinomial'))
m.train(Xtr, ytr)
preds = m.predict(Xte)

In [149]:
accuracy = 1 - np.count_nonzero(yte - preds)/len(yte)
accuracy

0.5770408163265306